<a href="https://colab.research.google.com/github/chanchalr04/CodeAlpha-Internship/blob/main/Music_genration_with_python.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [99]:
pip install tensorflow keras numpy mido pretty_midi pygame


In [71]:
from google.colab import files
uploaded = files.upload()



Saving baby.mid to baby (2).mid


In [72]:
import mido
import numpy as np

def midi_to_notes(midi_file):
    mid = mido.MidiFile(midi_file)  # Load the MIDI file
    notes = []  # List to store notes

    for msg in mid:  # Loop through each MIDI message
        if msg.type == 'note_on':  # If it's a "note on" event
            notes.append(msg.note)

    return np.array(notes)  # Convert list to NumPy array

# Test with a sample MIDI file
notes = midi_to_notes("/content/baby.mid")
print(notes)


[57 60 65 ... 38 42 42]


In [73]:
from tensorflow.keras.utils import to_categorical

sequence_length = 20  # Number of notes in each training sample

# Create input-output pairs
X, y = [], []
for i in range(len(notes) - sequence_length):
    X.append(notes[i:i + sequence_length])
    y.append(notes[i + sequence_length])

# Convert to NumPy arrays
X, y = np.array(X), np.array(y)

# Normalize and reshape input
X = X / 127.0
X = np.expand_dims(X, axis=-1)

# One-hot encode output
y = to_categorical(y, num_classes=128)


In [74]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense

# Define the model
model = Sequential([
    LSTM(128, return_sequences=True, input_shape=(sequence_length, 1)),
    LSTM(128),
    Dense(128, activation='softmax')  # Output layer with 128 possible notes
])

model.compile(loss='categorical_crossentropy', optimizer='adam')

model.summary()  # See model architecture


Model: "sequential_8"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ lstm_16 (LSTM)                       │ (None, 20, 128)             │          66,560 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ lstm_17 (LSTM)                       │ (None, 128)                 │         131,584 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_8 (Dense)                      │ (None, 128)                 │          16,512 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 214,656 (838.50 KB)

 Trainable params: 214,656 (838.50 KB)

 Non-trainable params: 0 (0.00 B)

In [75]:
model.fit(X, y, epochs=50, batch_size=64)  # Adjust epochs as needed


Epoch 1/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 36s 58ms/step - loss: 3.6811
Epoch 2/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 10s 58ms/step - loss: 3.0540
Epoch 3/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 5s 52ms/step - loss: 3.0225
Epoch 4/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 6s 56ms/step - loss: 3.0175
Epoch 5/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 5s 52ms/step - loss: 3.0190
Epoch 6/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 6s 54ms/step - loss: 3.0478
Epoch 7/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 6s 55ms/step - loss: 3.0417
Epoch 8/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 5s 53ms/step - loss: 3.0449
Epoch 9/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 6s 57ms/step - loss: 3.0498
Epoch 10/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 10s 57ms/step - loss: 3.0549
Epoch 11/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 5s 53ms/step - loss: 3.0306
Epoch 12/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 6s 60ms/step - loss: 3.0482
Epoch 13/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 5s 51ms/step - loss: 3.0458
Epoch 14/50
101/101 ━━━━━━━━━━━━━━━━━━━━ 10s 52ms/step - loss: 3.0388
Epoch 15/50
101/101 ━━━━━━━━━━━━━━━━━━━

In [76]:
import random

def generate_music(model, seed_notes, length=100):
    output = list(seed_notes)  # Start with seed notes

    for _ in range(length):
        input_seq = np.array(output[-sequence_length:]) / 127.0  # Normalize
        input_seq = np.expand_dims(input_seq, axis=0)  # Reshape for LSTM

        prediction = model.predict(input_seq)  # Predict next note
        next_note = np.argmax(prediction)  # Choose the most probable note

        output.append(next_note)  # Append to sequence

    return output

# Generate music using a random seed
seed_notes = [random.randint(40, 80) for _ in range(sequence_length)]
generated_notes = generate_music(model, seed_notes, length=100)
print(generated_notes)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 294ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━

In [78]:
from mido import MidiFile, MidiTrack, Message

def notes_to_midi(notes, filename="output.mid"):
    mid = MidiFile()
    track = MidiTrack()
    mid.tracks.append(track)

    for note in notes:
        track.append(Message('note_on', note=note, velocity=64, time=120))
        track.append(Message('note_off', note=note, velocity=64, time=120))

    mid.save(filename)
    print(f"Saved as {filename}")

notes_to_midi(generated_notes)


Saved as output.mid


In [79]:
!apt-get install fluidsynth
!pip install mido python-rtmidi


Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
fluidsynth is already the newest version (2.2.5-1).
0 upgraded, 0 newly installed, 0 to remove and 29 not upgraded.


In [88]:
import os
os.environ["SDL_AUDIODRIVER"] = "dummy"  # Headless mode
import pygame

pygame.init()
pygame.mixer.init()
print(pygame.mixer.get_init())  # Should print some audio settings


(44100, -16, 2)


In [86]:
import pygame
pygame.init()
print(pygame.mixer.get_init())


(44100, -16, 2)


In [87]:
!apt-get install fluidsynth


Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
fluidsynth is already the newest version (2.2.5-1).
0 upgraded, 0 newly installed, 0 to remove and 29 not upgraded.


In [83]:
!fluidsynth -ni soundfont.sf2 output.mid -F output.wav -r 44100


FluidSynth runtime version 2.2.5
Copyright (C) 2000-2022 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of Creative Technology Ltd.

fluidsynth: error: fluid_is_soundfont(): fopen() failed: 'File does not exist.'
Parameter 'soundfont.sf2' not a SoundFont or MIDI file or error occurred identifying it.
Rendering audio to file 'output.wav'..


In [85]:
from IPython.display import Audio
Audio("output.wav")